In [259]:
from hakai_profile_qc import show
from hakai_api import Client
import pandas as pd

import plotly.express as px
from plotly.subplots import make_subplots

import ipywidgets as widgets
from ipywidgets import interact_manual, VBox, HBox
from IPython.display import display

# Connect to Hakai API and retrieve data

In [376]:
# Set hakai authorization and retrieve data
client = Client()
server = "goose"
endpoint = "ctd/views/file/cast/data"
query = "station=QU39&limit=-1&start_dt>2018-01-01"
url = f"https://{server}.hakai.org/api/{endpoint}?{query}"
response = client.get(url)

if response.status_code != 200:
    response.raise_for_status()
df = pd.DataFrame(response.json())

In [377]:
def generate_multiindex_columns(columns):
    # Rename hakai columns to multilevel columns
    new_columns = []
    for var in columns:
        if var.endswith("flag_level_1"):
            new_columns += [(var[:-13], "QARTOD")]
        elif var.endswith("_flag"):
            new_columns += [(var[:-5], "FLAG")]
        else:
            new_columns += [(var, "Value")]
    return pd.MultiIndex.from_tuples(new_columns, names=["variable_name", "type"])


qartod_color_map = {
    "1": "green",
    "2": "purple",
    "3": "orange",
    "4": "red",
    "9": "pink",
}

df_plot = df.copy().set_index(["hakai_id", "direction_flag", "depth"])
df_plot.columns = generate_multiindex_columns(df_plot.columns)

hakai_ids_list = df_plot.index.get_level_values(0).drop_duplicates()
variable_list = [
    var[0]
    for var in df_plot.columns
    if var[1] == "QARTOD" and var[0] not in ("process", "location", "depth", "pressure")
]

# Plot profile

In [382]:
# Define interface
selected_hakai_ids = widgets.SelectMultiple(
    description="Hakai ID", options=hakai_ids_list, value=[hakai_ids_list[0]]
)
x = widgets.SelectMultiple(
    description="Variable(s)",
    options=variable_list,
    value=(
        "temperature",
        "salinity",
        "dissolved_oxygen_ml_l",
        "flc",
        "turbidity",
        "par",
    ),
)
y = widgets.Dropdown(
    description="Y Axis",
    options=["depth", "pressure", "measurement_dt"],
    select="depth",
)
show_upcast = widgets.ToggleButton(value=False, description="Show Upcast")
ui = VBox((HBox((selected_hakai_ids, x, y)), show_upcast))


# Make figure
# @interact(selected_hakai_ids=selected_hakai_ids,x=x,show_upcast=show_upcast)
def generate_profile_plot(selected_hakai_ids, x, show_upcast):
    """Plot profile data"""
    direction_flag = ["d"]
    if show_upcast:
        direction_flag += ["u"]

    data = df_plot.query(
        "hakai_id in @selected_hakai_ids and direction_flag in @direction_flag"
    )

    fig = px.scatter(
        data[list(x)].stack(level=0).reset_index().astype({"QARTOD": str}),
        x="Value",
        y="depth",
        color="QARTOD",
        symbol="direction_flag",
        facet_col="variable_name",
        hover_data=["hakai_id", "FLAG"],
        color_discrete_map=qartod_color_map,
    )
    fig.update_yaxes(autorange="reversed")
    # Swap title to xaxis
    for id, annotation in enumerate(fig.layout.annotations):
        fig.layout[f"xaxis{id+1}"].title.text = annotation.text.replace(
            "variable_name=", ""
        )
        annotation.text = ""
    fig.update_xaxes(matches=None)
    return fig

In [383]:
interact_manual(
    generate_profile_plot,
    selected_hakai_ids=selected_hakai_ids,
    x=x,
    show_upcast=show_upcast,
)

interactive(children=(SelectMultiple(description='Hakai ID', index=(0,), options=('01907674_2018-01-09T18:14:2…

<function __main__.generate_profile_plot(selected_hakai_ids, x, show_upcast)>

# Plot Time Series

In [381]:
timeseries_variable = widgets.Dropdown(options=variable_list, value="temperature")


def generate_timeseries(variable):
    fig = px.scatter(
        df.dropna(subset=[variable]),
        x="measurement_dt",
        y="depth",
        color=variable,
        symbol=f"{variable}_flag_level_1",
        hover_data=["hakai_id", f"{variable}_flag"],
        range_color=df[variable].quantile([0.05, 0.95]).tolist(),
    )

    fig.update_yaxes(autorange="reversed")
    fig.update_layout(
        legend=dict(yanchor="bottom", y=1.04, xanchor="right", x=1, orientation="h")
    )
    return fig


interact_manual(generate_timeseries, variable=timeseries_variable)

interactive(children=(Dropdown(description='variable', index=1, options=('conductivity', 'temperature', 'par',…

<function __main__.generate_timeseries(variable)>